In [1]:
import networkx as nx
import numpy as np
import os.path as op
import scipy as sp

import os
import csv

from collections import OrderedDict
from sklearn.preprocessing import normalize
from sklearn.neighbors import DistanceMetric
from scipy.linalg import svd
from scipy.linalg import norm

np.random.seed(12345678)  # for reproducibility, set random seed

In [15]:
path = '/Users/gkiar/code/ocp/ndmg-paper/data/'
# dsets = ['BNU1', 'BNU3', 'KKI2009', 'MRN114', 'MRN1313', 'NKI1', 'NKIENH', 'SWU4']
dsets = ['BNU1', 'BNU3', 'KKI2009', 'NKI1', 'SWU4']
# dsets = ['KKI2009']
# dsets = ['SWU4']

dir_names = [path + '/' + d for d in dsets]

N = 70

fs = OrderedDict()
for idx, dd in enumerate(dsets):
    fs[dd] = [root + "/" + fl for root, dirs, files in os.walk(dir_names[idx])
              for fl in files if fl.endswith(".graphml")]

ps = {os.path.splitext(os.path.basename(fl))[0] : root + "/" + fl
      for root, dirs, files in os.walk(path+'phenotypes')
      for fl in files if fl.endswith(".csv") }

print "Datasets: " + ", ".join([fkey + ' (' + str(len(fs[fkey])) + ')'
                                for fkey in fs])
S = sum([len(fs[key]) for key in fs])
print "Total Subjects: %d" % (S)

Datasets: BNU1 (81), BNU3 (46), KKI2009 (42), NKI1 (37), SWU4 (453)
Total Subjects: 659


In [3]:
def loadGraphs(filenames, verb=False):
    """
    Given a list of files, returns a dictionary of graphs

    Required parameters:
        filenames:
            - List of filenames for graphs
    Optional parameters:
        verb:
            - Toggles verbose output statements
    """
    #  Initializes empty dictionary
    gstruct = OrderedDict()
    for idx, files in enumerate(filenames):
        if verb:
            print "Loading: " + files
        #  Adds graphs to dictionary with key being filename
        fname = os.path.basename(files)
        gstruct[fname] = nx.read_graphml(files)
    return gstruct

def constructGraphDict(names, fs, verb=False):
    """
    Given a set of files and a directory to put things, loads graphs.

    Required parameters:
        names:
            - List of names of the datasets
        fs:
            - Dictionary of lists of files in each dataset
    Optional parameters:
        verb:
            - Toggles verbose output statements
    """
    #  Loads graphs into memory for all datasets
    graphs = OrderedDict()
    for idx, name in enumerate(names):
        if verb:
            print "Loading Dataset: " + name
        # The key for the dictionary of graphs is the dataset name
        graphs[name] = loadGraphs(fs[name], verb=verb)
    return graphs

In [4]:
graphs = constructGraphDict(dsets, fs, verb=False)

In [5]:
mat = np.zeros((N, N, S))
ids = []
c = 0

print "Initial shape: ", mat.shape, S

for dset in graphs.keys():
    for subj in graphs[dset].keys():
        ids += [subj.split("_")[1]]
        
        tmpg = np.array(nx.adj_matrix(graphs[dset][subj]).todense())
        ratio = np.sum(tmpg > 0)*1.0 / N / N
        mat[:, :, c] = tmpg
        c += 1
#         if ratio > 0.2 and ratio < 0.85 and np.max(tmpg) < 1e5 and np.sum(tmpg) > 1e5:
#             mat[:, :, c] = tmpg
#             c += 1
#         else:
#             mat = mat[:,:,0:mat.shape[2]-1]
#             print ids[-1]
#             print ids[-2]
#             del ids[-1]
print "Shape after minor pruning: ", mat.shape, len(ids)

Initial shape:  (70, 70, 659) 659
Shape after minor pruning:  (70, 70, 659) 659


In [6]:
def partial_disc(D, labels, subject, trial1, trial2):
    enum = np.arange(D.shape[0])
    idx1 = [i for i, x in enumerate(labels) if x == subject]
    t1 = enum[idx1][trial1]
    t2 = enum[idx1][trial2]
    d_t1_t2 = D[t1][t2]
    
    idx2 = [i for i, x in enumerate(labels) if x != subject]
    d_ra = [D[t1][x] for x in enum[idx2]]
    
    return np.mean(d_t1_t2 < d_ra)

def distance_matrix(data, metric, symmetric = True):
    n = data.shape[2]
    dist_matrix = np.zeros((n, n))
    if symmetric:
        for i in range(n):
            for j in range(i):
                tmp = metric(data[:,:,i] - data[:,:,j])
                dist_matrix[i][j] = tmp
                dist_matrix[j][i] = tmp
    else:
        for i in range(n):
            for j in range(n):
                dist_matrix[i][j] = metric(data[i] - data[j])
    return dist_matrix

def discriminibility(data, labels, metric):
    dist_matrix = distance_matrix(data, metric)
    partials = []
    for s in list(set(labels)):
        num = ids.count(s)
        for t in range(num):
            for tt in range(num):
                if tt != t:
                    p = partial_disc(dist_matrix, labels, s, t, tt)
                    partials.append(p)
    return dist_matrix, np.mean(partials)

In [7]:
dist, disc = discriminibility(mat, ids, norm)
print disc

0.915656682919


In [17]:
import ndmg.stats.plotly_helper as plh
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot, plot

sizes = [len(graphs[dset].keys()) for dset in graphs.keys()]
cumul = [0] + [np.sum(sizes[:i+1])-1 for i in range(len(sizes))]

init_notebook_mode()
myplot = plh.plot_heatmap(np.log10(dist))
myplot.layout.title = "Multi-Study Distance Plot Using Desikan Atlas"
myplot.layout.width = 1000
myplot.layout.height = 1000
myplot.layout.yaxis.autorange = 'reversed'
myplot.layout.yaxis.tickvals = cumul
myplot.layout.xaxis.tickvals = cumul
myplot.layout.yaxis.ticktext = ['' for i in range(len(cumul))]
myplot.layout.xaxis.ticktext = ['' for i in range(len(cumul))]
myplot.layout.yaxis.ticklen = 15
myplot.layout.xaxis.ticklen = 15
myplot.layout.yaxis.tickwidth = 3
myplot.layout.xaxis.tickwidth = 3

anno = []
for idx in range(len(cumul)-1):
    anno += [dict(x= -0.07,
                  y=1.025-(cumul[idx]+(cumul[idx+1]-cumul[idx])/2.0)/S,
                  xref='paper',
                  yref='paper',
                  text=graphs.keys()[idx],
                  showarrow=False,
                  font=dict(color='rgba(0.0,0.0,0.0,1)',
                            size=14)),
             dict(x= -0.07,
                  y=1.003-(cumul[idx]+(cumul[idx+1]-cumul[idx])/2.0)/S,
                  xref='paper',
                  yref='paper',
                  text='(N={})'.format(len(graphs.values()[idx])),
                  showarrow=False,
                  font=dict(color='rgba(0.0,0.0,0.0,1)',
                            size=14))
           ]
myplot.layout.annotations = anno
iplot(myplot)